In [1]:
# 불필요한 라벨링 파일을 제외하고 필요한 파일들만 남음
# 이 중 미스라벨링 파일을 찾아 제거해야됨
import time
import numpy as np
from glob import glob
import pandas as pd
from PIL import Image
import random
import math
from tqdm import tqdm
from threading import Thread

In [2]:
images = glob('../../../datasets/aihub_safety/human_car_ver2/images/*')
labels = glob('../../../datasets/aihub_safety/human_car_ver2/labels/*')

In [3]:
print(len(images))
print(len(labels))

925106
925106


In [4]:
images.sort()
labels.sort()
random.seed(42)
random.shuffle(images)
random.seed(42)
random.shuffle(labels)

In [5]:
print(images[:3])
labels[:3]

['../../../datasets/aihub_safety/human_car_ver2/images/S2-N1901M18386.jpg', '../../../datasets/aihub_safety/human_car_ver2/images/S2-N1803M07141.jpg', '../../../datasets/aihub_safety/human_car_ver2/images/S2-N0508M47833.jpg']


['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N1901M18386.txt',
 '../../../datasets/aihub_safety/human_car_ver2/labels/S2-N1803M07141.txt',
 '../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt']

In [6]:
clsdict = {i+1 : [] for i in range(19)}

# pd.DataFrame({'cls' : list(cls),'resulution' : resolution , 'width' : width, 'height' : height , 'ratio' : w_perh , 'v' : v , 'rmg' : rmg , 'rmb' : rmb , 'gmb' : gmb})


# [filename,resolution, width, height, ratio, w_perh, h,s,v,rmg,rmb,gmb]

In [7]:
def xywh2xyxy(xywh,w,h, rounding = True):
    xywh = [float(i) for i in xywh]

    if rounding:
        xyxy = [round((xywh[0] - xywh[2]/2) * w),round((xywh[1] - xywh[3]/2) * h),round((xywh[0] + xywh[2]/2) * w),round((xywh[1] + xywh[3]/2) * h)]
        if xyxy[0] > xyxy[2]:
            temp = xyxy[0]
            xyxy[0] = xyxy[2]
            xyxy[2] = temp
        if xyxy[1] > xyxy[3]:
            temp = xyxy[1]
            xyxy[1] = xyxy[3]
            xyxy[1] = temp
        return xyxy
    else:
        return [(xywh[0] - xywh[2]/2) * w ,(xywh[1] - xywh[3]/2) * h ,(xywh[0] + xywh[2]/2) * w ,(xywh[1] + xywh[3]/2) * h]

In [8]:
img = Image.open(images[0])

In [9]:
img.size

(1920, 1080)

In [31]:
errorflie = []
sum = 0
def make_df(labels,results,p):
    sum = 0
    clsdict = {i+1 : [] for i in range(19)}

    for k,i in tqdm(enumerate(labels)):
       
        with open(i, 'r' ) as f:
            datas = f.readlines()
        for j in datas:
            cls = j.split(' ')[0]
            box = j.split(' ')[1:]
            
            try:
                img = Image.open(images[k])
            except:
                errorflie.append(i)

            xyxy = xywh2xyxy(box, img.size[0], img.size[1])

            # boxed_img = img.crop((xyxy[0],xyxy[1],xyxy[2],xyxy[3]))

            width = xyxy[2] - xyxy[0] + 1 # boxed img width, height
            height = xyxy[3] - xyxy[1] + 1 

            resolution = round(math.sqrt(width * height))
            w_perh = width / height
            
            filename = i

            sum+=1

            clsdict[int(cls)+1].append([filename,resolution,width,height,w_perh])

    results[p] = [clsdict,sum]


In [32]:
# results = [None]
# make_df(labels[1:10],results,0)

9it [00:00, 4446.78it/s]


In [36]:
n = 12
start_idx = 0
end_idx = len(labels) 
indice = list(range(start_idx,end_idx,end_idx//n))
indice[-1] = end_idx

In [37]:
indice

[0,
 77092,
 154184,
 231276,
 308368,
 385460,
 462552,
 539644,
 616736,
 693828,
 770920,
 848012,
 925106]

In [25]:
import pickle

# save data
with open('user.pickle','wb') as fw:
    pickle.dump(clsdict, fw)


In [38]:
results = [None] * n
threads = [None] * n
for i in range(n):
    temp_labels = labels[indice[i]:indice[i+1]]
    threads[i] = Thread(target=make_df,args=(temp_labels,results,i) )
    threads[i].start()
for i in range(len(threads)):
    threads[i].join()


0it [00:00, ?it/s]





















































13it [00:00, 128.67it/s]






















































26it [00:00, 113.89it/s]

























































45it [00:00, 137.61it/s]






















































60it [00:00, 141.12it/s]






















































75it [00:00, 125.54it/s]






















































89it [00:00, 127.11it/s]






















































103it [00:00, 130.11it/s][A






















































126it [00:00, 152.63it/s][A







































148it [00:01, 170.30it/s]




















































166it [00:01, 170.21it/s]







































































184it [00:01, 150.99it/s]



















































202it [00:01, 157.80it/s]

























In [42]:
results[0]

[{1: [['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    91,
    70,
    119,
    0.5882352941176471],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    68,
    61,
    75,
    0.8133333333333334],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    41,
    26,
    65,
    0.4],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    138,
    99,
    192,
    0.515625],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    104,
    68,
    159,
    0.4276729559748428],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    42,
    37,
    48,
    0.7708333333333334],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M47833.txt',
    82,
    63,
    106,
    0.5943396226415094],
   ['../../../datasets/aihub_safety/human_car_ver2/labels/S2-N0508M36428.txt',
    245,
    250,
    240,
    1.04166666

In [43]:
sum = 0
for i in results:
    sum += i[1]
print(sum)


5216750


In [46]:

clsdict = {i+1 : [] for i in range(19)}
for i  in results:
    for j in range(19):
        clsdict[j+1] += i[0][j+1]

In [45]:
indice

[0,
 77092,
 154184,
 231276,
 308368,
 385460,
 462552,
 539644,
 616736,
 693828,
 770920,
 848012,
 925106]

In [48]:
import pickle

# load data
with open('clsdict.pickle', 'wb') as fr:
    pickle.dump(clsdict,fr)